In [1]:
# NextPNR Parameter Sweep with MLIR Processing Pipeline
# Comprehensive tool for FPGA parameter optimization using MLIR-generated benchmarks

# Enable auto reload for imports
%load_ext autoreload
%autoreload 2

# Standard library imports
import subprocess
import os
import sys
import re
import time
import json
from pathlib import Path
from datetime import datetime
import itertools
import concurrent.futures

# Third-party imports
import pandas as pd
import numpy as np
from loguru import logger

# Configure loguru logger - output only to stdout (only if not already configured)
# logger.remove()  # Remove default handler
# logger.add(sys.stdout, format="{time} | {level} | {message}", level="INFO")

print("=== NextPNR Parameter Sweep with MLIR Processing Pipeline ===")
print("Comprehensive FPGA parameter optimization using MLIR-generated benchmarks")
print("Auto-reload enabled for module imports")

print("✓ Core libraries and logging configured")

=== NextPNR Parameter Sweep with MLIR Processing Pipeline ===
Comprehensive FPGA parameter optimization using MLIR-generated benchmarks
Auto-reload enabled for module imports
✓ Core libraries and logging configured


In [2]:
# Configuration and Parameter Setup
# Define parameter ranges, paths, and constants for the parameter sweep

import numpy as np
import os
from pathlib import Path

# Define parameter ranges for the sweep
CONNECTIVITY_FACTORS = np.arange(0.0, 2.0, 0.2)  # 0.0 to 2.0 with step 0.2
CONGESTION_FACTORS = np.arange(0.0, 2.0, 0.2)    # 0.0 to 2.0 with step 0.2

# Create parameter grid - use reduced set for testing or full grid for production
# grid = list(itertools.product(CONNECTIVITY_FACTORS, CONGESTION_FACTORS))  # Full grid
grid = [(0, 0), (0, 1), (1, 0), (1, 1)]  # Reduced grid for testing

# software dir configuration
CALYX_PATH: str = "/home/kelvin/calyx"
MLIR_OPT_PATH: str = "/home/kelvin/circt/build/vscode/bin/mlir-opt"
HLSTOOL_PATH: str = "/home/kelvin/circt/build/vscode/bin/hlstool"

# Project and directory configuration
MY_FAB_ROOT: Path = Path("/home/kelvin/FABulous_fork")
FAB_PROJ_DIR: Path = Path("/home/kelvin/FABulous_fork/myProject")

# Compilation results directory structure - Stage-based organization
COMPILATION_RESULT_DIR: Path = Path("/home/kelvin/FABulous_fork/myProject/PnR/compilation_result")

# Stage-specific directories for cleaner organization and simpler naming
MLIR_OPTIMIZED_DIR: Path = COMPILATION_RESULT_DIR / "01_optimized_mlir"
MLIR_EXTRACTED_DIR: Path = COMPILATION_RESULT_DIR / "02_extracted_mlir"
FUTIL_OUTPUT_DIR: Path = COMPILATION_RESULT_DIR / "03_futil"
VERILOG_OUTPUT_DIR: Path = COMPILATION_RESULT_DIR / "04_verilog"
OUTPUT_DIR: Path = Path("/home/kelvin/FABulous_fork/myProject/PnR/parameter_sweep_results")

# Benchmark directory configuration - MLIR files only
BENCHMARK_ROOT_DIR: Path = Path("/home/kelvin/FABulous_fork/myProject/PnR/mlir")

# Set up environment variables
os.environ["FAB_PROJ_DIR"] = str(FAB_PROJ_DIR)
os.environ["PATH"] = f"/home/kelvin/nextpnr/build/bba:{os.environ['PATH']}"
os.environ["PATH"] = f"/home/kelvin/nextpnr/build:{os.environ['PATH']}"
os.environ["PATH"] = f"/home/kelvin/yosys:{os.environ['PATH']}"
os.environ["PATH"] = f"/home/kelvin/circt/build/vscode/bin:{os.environ['PATH']}"
os.environ["CALYX_PRIMITIVES_DIR"] = str(Path(CALYX_PATH))

# Create necessary directories for all processing stages
COMPILATION_RESULT_DIR.mkdir(exist_ok=True)
MLIR_OPTIMIZED_DIR.mkdir(exist_ok=True)
MLIR_EXTRACTED_DIR.mkdir(exist_ok=True)
FUTIL_OUTPUT_DIR.mkdir(exist_ok=True)
VERILOG_OUTPUT_DIR.mkdir(exist_ok=True)
OUTPUT_DIR.mkdir(exist_ok=True)

# FABulous file paths
CHIPDB_PATH = FAB_PROJ_DIR / ".FABulous/hycube.bit"
JSON_INPUT = FAB_PROJ_DIR / "user_design/synth_test.json"
CONSTRAIN_PAIR = FAB_PROJ_DIR / ".FABulous/hycube_constrain_pair.inc"
FDC_PATH = FAB_PROJ_DIR / "user_design/test.fdc"

# Fallback source file if no generated Verilog files are available
FALLBACK_SOURCE_HDL = MY_FAB_ROOT / "benchmarks/userbench/loop_array_inner/loop_array_inner.sv"

# Fixed parameters for nextpnr runs
BETA_VALUE = 0.9
PLACE_TRIALS = 1
ROUTER_TIMEOUT = 20000

# Initialize available MLIR files and Verilog files structures
availableMlirFiles = []
availableVerilogFiles = []
benchmarkStructure = {}

print(f"Configuration setup complete:")
print(f"  Parameter combinations: {len(CONNECTIVITY_FACTORS)} × {len(CONGESTION_FACTORS)} = {len(CONNECTIVITY_FACTORS) * len(CONGESTION_FACTORS)} total")
print(f"  Test grid size: {len(grid)} combinations")
print(f"  Compilation results directory: {COMPILATION_RESULT_DIR}")
print(f"  Stage directories:")
print(f"    01_optimized_mlir/ - MLIR optimization results")
print(f"    02_extracted_mlir/ - Loop-to-function extraction results")
print(f"    03_intermediate_mlir/ - Individual function MLIR files")
print(f"    04_futil/ - Generated FUTIL files")
print(f"    05_verilog/ - Final Verilog output")
print(f"  Parameter sweep results directory: {OUTPUT_DIR}")
print(f"  Benchmark root directory: {BENCHMARK_ROOT_DIR}")
print(f"  Starting with unoptimized MLIR files from BENCHMARK folder")

print("✓ Configuration and paths set up successfully")

Configuration setup complete:
  Parameter combinations: 10 × 10 = 100 total
  Test grid size: 4 combinations
  Compilation results directory: /home/kelvin/FABulous_fork/myProject/PnR/compilation_result
  Stage directories:
    01_optimized_mlir/ - MLIR optimization results
    02_extracted_mlir/ - Loop-to-function extraction results
    03_intermediate_mlir/ - Individual function MLIR files
    04_futil/ - Generated FUTIL files
    05_verilog/ - Final Verilog output
  Parameter sweep results directory: /home/kelvin/FABulous_fork/myProject/PnR/parameter_sweep_results
  Benchmark root directory: /home/kelvin/FABulous_fork/myProject/PnR/mlir
  Starting with unoptimized MLIR files from BENCHMARK folder
✓ Configuration and paths set up successfully


In [3]:
# MLIR Processing Pipeline Configuration
# Set up the complete MLIR → FUTIL → Verilog processing pipeline starting with unoptimized MLIR files

import re
import os
from pathlib import Path
import subprocess


# MLIR Directory Configuration
MLIR_DIR = Path("mlir")

def findMlirBenchmarks(benchmarkDir: Path) -> list:
    """Find all .mlir files in the benchmark directory.

    Parameters
    ----------
    benchmarkDir : Path
        Path to the benchmark directory containing MLIR files.

    Returns
    -------
    list
        List of MLIR file paths found in the directory.
    """
    mlirFiles = []
    
    if benchmarkDir.exists():
        # Find all .mlir files directly in the benchmark directory
        mlirFiles = list(benchmarkDir.glob("*.mlir"))
        print(f"Found {len(mlirFiles)} MLIR files in {benchmarkDir}")
        for mlirFile in mlirFiles:
            print(f"  - {mlirFile.name}")
    else:
        logger.warning(f"Benchmark directory does not exist: {benchmarkDir}")
    
    return mlirFiles

def extractTopLevelFunctions(mlirFile: Path) -> list:
    """Extract all top-level functions from MLIR file.

    Parameters
    ----------
    mlirFile : Path
        Path to the MLIR file.

    Returns
    -------
    list
        List of function names found in the MLIR file.
    """
    # Generic function pattern to capture all functions
    funcPattern = re.compile(rf"func\s+@({mlirFile.stem}_inner_loop_\d+)\s*\(")
    try:
        with mlirFile.open("r") as file:
            content = file.read()
        matches = funcPattern.findall(content)
        print(f"Found functions in {mlirFile.name}: {matches}")
        return matches
        
    except Exception as e:
        logger.error(f"Error reading MLIR file {mlirFile}: {e}")
        return []


print("MLIR processing configuration complete")
print("✓ Function extraction configured for unoptimized MLIR files")
print("Next: Define modular pipeline functions")

MLIR processing configuration complete
✓ Function extraction configured for unoptimized MLIR files
Next: Define modular pipeline functions


In [4]:
# Modular Pipeline Functions
# Refactored processing steps to start with unoptimized MLIR files with race condition prevention

def stepOptimizeMlir(srcPath: Path, dstPath: Path) -> bool:
    """Step 1: Apply MLIR optimizations to unoptimized MLIR file.
    """
    print(f"Step 1: Applying MLIR optimizations: {srcPath.name}")
    optimizationCmd = [
        "mlir-opt",
        "--allow-unregistered-dialect",
        "--int-range-optimizations",
        "--sroa",
        "--normalize-memrefs", 
        "--flatten-memref",
        "--enable-loop-simplifycfg-term-folding",
        "--affine-loop-fusion",
        "--affine-simplify-structures",
        "--affine-loop-invariant-code-motion",
        "--affine-scalrep",
        "--affine-pipeline-data-transfer",
        "-mlir-print-op-generic",
        "-o", str(dstPath),
        str(srcPath)  # Input MLIR file
    ]
    
    print(f"Applying MLIR optimizations to {srcPath.name}")
    print("Optimizations: int-range, sroa, memref normalization, affine passes")
    
    result = subprocess.run(optimizationCmd, capture_output=True, text=True, timeout=300)
    if result.returncode != 0:
        logger.error(f"MLIR optimization failed for {srcPath.name}")
        logger.error(f"STDERR: {result.stderr}")
        return False
    
    # Verify the output file was created and has content
    waitTime = 0
    while (not dstPath.exists() or dstPath.stat().st_size == 0) and waitTime < 10:
        time.sleep(1)
        waitTime += 1

    if waitTime >= 10 or not dstPath.exists() or dstPath.stat().st_size == 0:
        logger.error(f"MLIR optimization output file {dstPath.name} was not created or is empty")
        return False

    print(f"✓ MLIR optimizations completed for {srcPath.name}")
    return True


In [5]:
import inner_loop_to_func

def stepConvertInnerLoops(srcPath: Path, dstPath: Path) -> bool:
    """Step 2: Convert inner loops to functions with race condition protection.
    """

    print(f"Step 2: Converting inner loops to functions: {srcPath.name} -> {dstPath.name}")
    tmpDstPath = dstPath.with_suffix(".tmp")

    try:
        result = inner_loop_to_func.process_mlir_file(str(srcPath), str(tmpDstPath))
    except Exception as e:
        logger.error(f"Inner loop conversion failed for {srcPath.name}: {e}")
        return False
    
    # Verify the output file was created and has content
    waitTime = 0
    while (not tmpDstPath.exists() or tmpDstPath.stat().st_size == 0) and waitTime < 10:
        time.sleep(1)
        waitTime += 1

    if waitTime >= 10 or not tmpDstPath.exists() or tmpDstPath.stat().st_size == 0:
        logger.error(f"Extracted output file {tmpDstPath.name} was not created or is empty")
        return False
    
    optCmd = [
            "mlir-opt",
            str(tmpDstPath),  # Use temporary file for validation
            "-o", str(dstPath)
        ]
    
    result = subprocess.run(optCmd, capture_output=True, text=True, timeout=300)
    
    tmpDstPath.unlink(True)

    if result.returncode == 0:
        print(f"✓ Inner loop conversion and MLIR round trip completed for {dstPath.name}")

    # Verify the output file was created and has content
    waitTime = 0
    while (not dstPath.exists() or dstPath.stat().st_size == 0) and waitTime < 10:
        time.sleep(1)
        waitTime += 1

    if waitTime >= 10 or not dstPath.exists() or dstPath.stat().st_size == 0:
        logger.error(f"Round tripping {tmpDstPath} to {dstPath.name} failed")
        return False
    
    return True


In [6]:

def stepMlirToFutil(mlirPath: Path, futilPath: Path) -> list:
    """Step 3: Convert MLIR to Calyx FUTIL format using CIRCT with race condition protection.
    """
    print(f"Step 3: Converting MLIR to FUTIL: {mlirPath.name} -> multiple FUTIL files")

    extractedFunctions = extractTopLevelFunctions(mlirPath)
    print(f"Found {len(extractedFunctions)} functions to extract: {extractedFunctions}")
    
    generatedFutilFiles = []
    
    for funcName in extractedFunctions:
        # Create clean FUTIL filename for each function 
        # For main functions: use baseName_funcName (e.g., nw_nw_nw_nw)
        # For inner loop functions: use funcName directly (e.g., nw_nw_inner_loop_1)
        
        funcFutilPath = futilPath.parent / f"{funcName}.futil"
        funcMlirPath = futilPath.parent / f"{funcName}.mlir"

        print(f"Processing function '{funcName}' -> {funcFutilPath.name}")

        try:
            # Use retry mechanism for hlstool command
            hlstoolCmd = [
                "hlstool", 
                "--calyx-hw", 
                "--output-level=core", 
                "--ir", 
                "--allow-unregistered-dialects", 
                f"--top-level-function={funcName}",
                str(mlirPath),
                "-o", str(funcMlirPath)
            ]

            result = subprocess.run(hlstoolCmd, capture_output=True, text=True, timeout=30)
            
            if result.returncode != 0:
                raise RuntimeError(f"hlstool failed: {result.stderr}")
                
            print(f"✓ hlstool completed for function '{funcName}'")
            
            # Step 2: fud2 command to convert to FUTIL with retry
            translateCmd = [
                "circt-translate", 
                str(funcMlirPath), 
                "-o", str(funcFutilPath), 
                "--export-calyx"
            ]

            result = subprocess.run(translateCmd, capture_output=True, text=True, timeout=60)
            
            if result.returncode != 0:
                raise RuntimeError(f"circt-translate failed: {result.stderr}")
                
            print(f"circt-translate completed: {funcMlirPath.name} -> {funcFutilPath.name}")
            generatedFutilFiles.append(funcFutilPath)
            
            # Clean up intermediate MLIR file to save space
            funcMlirPath.unlink(missing_ok=True)
            
        except Exception as e:
            logger.error(f"Error processing function '{funcName}': {e}")
            # Clean up any partial files
            funcMlirPath.unlink(missing_ok=True)
            funcFutilPath.unlink(missing_ok=True)
            continue
    
    print(f"✓ MLIR to FUTIL conversion completed: {len(generatedFutilFiles)}/{len(extractedFunctions)} functions successful")
    return generatedFutilFiles


In [7]:

def stepFutilToVerilog(futilFiles: list, verilogBasePath: Path) -> list:
    """Step 4: Convert FUTIL files to Verilog using Calyx.
    
    This step processes multiple FUTIL files and generates corresponding Verilog files.

    Parameters
    ----------
    futilFiles : list
        List of FUTIL file paths to convert
    verilogBasePath : Path
        Base path for the output Verilog files (will be modified for each FUTIL file)

    Returns
    -------
    list
        List of successfully generated Verilog file paths, empty list if all failed
    """
    print(f"Step 4: Converting {len(futilFiles)} FUTIL files to Verilog")
    
    generatedVerilogFiles = []
    
    for futilPath in futilFiles:
        # Create simplified Verilog filename - use just the FUTIL file name
        verilogPath = verilogBasePath.parent / f"{futilPath.stem}.sv"
        
        # Calyx compilation command with proper library path
        calyxCmd = [
            "/home/kelvin/calyx/target/debug/calyx",
            "-l", "/home/kelvin/calyx",  # Add library path
            "-p", "fsm-opt",
            "-x", "simplify-with-control:without-register",
            "-x", "static-inline:offload-pause=false",
            "-p", "lower",
            "--nested",
            "-d", "papercut",
            "-d", "cell-share",
            "-o", str(verilogPath),
            "-b", "verilog",
            "--synthesis",
            str(futilPath)
        ]
        
        print(f"Running Calyx: {' '.join(calyxCmd)}")
        env = os.environ.copy()
        result = subprocess.run(calyxCmd, capture_output=True, text=True, timeout=300, cwd=CALYX_PATH, env=env)

        if result.returncode != 0:
            logger.error(f"Calyx failed for {futilPath.name}: {result.stderr}")
            continue  # Skip this file, continue with others
        
        if not verilogPath.exists():
            logger.error(f"Verilog file not created: {verilogPath}")
            continue  # Skip this file, continue with others
        
        generatedVerilogFiles.append(verilogPath)
        print(f"✓ Generated: {verilogPath.name}")
    
    if generatedVerilogFiles:
        print(f"✓ FUTIL to Verilog: {len(generatedVerilogFiles)}/{len(futilFiles)} files successful")
    else:
        logger.error(f"✗ No Verilog files generated from {len(futilFiles)} FUTIL files")
    
    return generatedVerilogFiles


In [8]:

def mlirPipeline(mlirSrc: Path, verilogDst: Path) -> list:
    """Master pipeline function that processes an unoptimized MLIR file through the complete pipeline.

    This function orchestrates the complete MLIR → FUTIL → Verilog pipeline:
    1. Apply MLIR optimizations to unoptimized MLIR file
    2. Convert inner loops to functions (optional)
    3. Convert MLIR to FUTIL using CIRCT (can generate multiple FUTIL files)
    4. Convert FUTIL to Verilog using Calyx (generates multiple Verilog files)

    Parameters
    ----------
    mlirSrc : Path
        Path to the unoptimized MLIR file
    verilogDst : Path
        Base path for the output Verilog files (will be modified for each function)

    Returns
    -------
    list
        List of successfully generated Verilog file paths, empty list if pipeline failed
    """
    print(f"=== Starting MLIR Pipeline: {mlirSrc.name} ===")
    
    # Validate input
    if not mlirSrc.exists():
        logger.error(f"MLIR file does not exist: {mlirSrc}")
        return []
    
    if not mlirSrc.suffix == ".mlir":
        logger.error(f"Source file must be a .mlir file: {mlirSrc}")
        return []
    
    # Create intermediate file paths using stage-specific directories for cleaner naming
    baseName = mlirSrc.stem
    
    # Stage 1: Optimized MLIR files
    optimizedMlirPath = MLIR_OPTIMIZED_DIR / f"{baseName}.mlir"
    
    # Stage 2: Extracted MLIR files (with loop-to-function conversion)
    extractedMlirPath = MLIR_EXTRACTED_DIR / f"{baseName}.mlir"
    
    # Stage 3: Base path for FUTIL files (actual files will have function names)
    futilBasePath = FUTIL_OUTPUT_DIR / f"{baseName}.futil"
    
    # Ensure output directories exist
    verilogDst.parent.mkdir(parents=True, exist_ok=True)
    MLIR_OPTIMIZED_DIR.mkdir(parents=True, exist_ok=True)
    MLIR_EXTRACTED_DIR.mkdir(parents=True, exist_ok=True)
    FUTIL_OUTPUT_DIR.mkdir(parents=True, exist_ok=True)
    
    try:
        # Step 1: Optimize MLIR
        if not stepOptimizeMlir(mlirSrc, optimizedMlirPath):
            logger.error(f"Pipeline failed at step 1 (optimize MLIR) for {mlirSrc.name}")
            return []
        
        # Step 2: Convert inner loops (optional - continue if this fails)
        if not stepConvertInnerLoops(optimizedMlirPath, extractedMlirPath):
            logger.error(f"Pipeline failed at step 2 (convert inner loops) for {mlirSrc.name}")
            return []

        # Step 3: MLIR to FUTIL (can generate multiple FUTIL files)
        futilFiles = stepMlirToFutil(extractedMlirPath, futilBasePath)
        if not futilFiles:
            logger.error(f"Pipeline failed at step 3 (MLIR to FUTIL) for {mlirSrc.name}")
            return []
        
        # Step 4: FUTIL to Verilog (processes multiple FUTIL files) - output goes to Verilog directory
        verilogFiles = stepFutilToVerilog(futilFiles, verilogDst)
        if not verilogFiles:
            logger.error(f"Pipeline failed at step 4 (FUTIL to Verilog) for {mlirSrc.name}")
            return []
        
        
        print(f"✅ Pipeline completed: {mlirSrc.name} → {len(verilogFiles)} Verilog files")
        return verilogFiles
        
    except Exception as e:
        logger.error(f"Pipeline failed with exception for {mlirSrc.name}: {e}")
        return []


In [9]:

def processBenchmarkMlir(mlirFile: Path, verilogOutputDir: Path) -> list:
    """Process a single MLIR benchmark file using the pipeline.

    Parameters
    ----------
    mlirFile : Path
        Path to the MLIR benchmark file
    verilogOutputDir : Path
        Directory to store the generated Verilog files

    Returns
    -------
    list
        List of successfully generated Verilog file paths
    """
    benchmarkName = mlirFile.stem
    
    # Generate base output Verilog filename in the Verilog output directory
    verilogBaseFileName = f"{benchmarkName}.sv"
    verilogOutputBasePath = verilogOutputDir / verilogBaseFileName
    
    # Run the complete pipeline (returns list of generated Verilog files)
    pipelineResults = mlirPipeline(mlirFile, verilogOutputBasePath)
    return pipelineResults

def processAllMlirBenchmarks() -> list:
    """Process all MLIR benchmarks using the pipeline.

    Returns
    -------
    list
        List of all successfully generated Verilog file paths
    """
    print("Starting MLIR pipeline processing for all benchmarks...")
    
    # Find all MLIR files in the benchmark directory
    mlirFiles = findMlirBenchmarks(BENCHMARK_ROOT_DIR)
    if not mlirFiles:
        logger.warning(f"No MLIR files found in {BENCHMARK_ROOT_DIR}")
        return []
    
    # Create output directories for all processing stages
    VERILOG_OUTPUT_DIR.mkdir(parents=True, exist_ok=True)
    MLIR_OPTIMIZED_DIR.mkdir(parents=True, exist_ok=True)
    MLIR_EXTRACTED_DIR.mkdir(parents=True, exist_ok=True)
    FUTIL_OUTPUT_DIR.mkdir(parents=True, exist_ok=True)
    
    print(f"Found {len(mlirFiles)} MLIR files to process")
    print(f"Output structure:")
    print(f"  Verilog files: {VERILOG_OUTPUT_DIR}")
    print(f"  Stage-based intermediate files in compilation_result/01-05 directories")
    
    allGeneratedVerilog = []
    for mlirFile in mlirFiles:
        generatedFiles = processBenchmarkMlir(mlirFile, verilogOutputDir)
        allGeneratedVerilog.extend(generatedFiles)
    
    print(f"MLIR pipeline completed: {len(allGeneratedVerilog)} Verilog files generated from {len(mlirFiles)} MLIR files")

    return allGeneratedVerilog

print("MLIR pipeline functions defined")
print("✓ Master function: mlirPipeline(mlirSrc: Path, verilogDst: Path) -> list")
print("✓ Individual steps: stepOptimizeMlir, stepConvertInnerLoops, stepMlirToFutil, stepFutilToVerilog")
print("✓ Batch processing: processBenchmarkMlir, processAllMlirBenchmarks")
print(f"✓ Starting with unoptimized MLIR files from: {BENCHMARK_ROOT_DIR}")
print(f"✓ Output structure: compilation_result/01-05 stage directories")

MLIR pipeline functions defined
✓ Master function: mlirPipeline(mlirSrc: Path, verilogDst: Path) -> list
✓ Individual steps: stepOptimizeMlir, stepConvertInnerLoops, stepMlirToFutil, stepFutilToVerilog
✓ Batch processing: processBenchmarkMlir, processAllMlirBenchmarks
✓ Starting with unoptimized MLIR files from: /home/kelvin/FABulous_fork/myProject/PnR/mlir
✓ Output structure: compilation_result/01-05 stage directories


In [10]:
# Improved Parallel Processing with Race Condition Prevention
# Enhanced parallel MLIR processing with better error handling and synchronization

import concurrent.futures
import threading
from typing import Callable, List, Tuple, Any

def processWithSafeParallel(
    items: List[Path], 
    processFunc: Callable[[Path], Any], 
    maxWorkers: int = 4,
    description: str = "Processing"
) -> List[Tuple[Path, Any, bool]]:
    """Process a list of items in parallel with race condition protection.
    
    Parameters
    ----------
    items : List[Path]
        List of items to process
    processFunc : Callable
        Function to apply to each item
    maxWorkers : int
        Maximum number of parallel workers
    description : str
        Description for logging
    
    Returns
    -------
    List[Tuple[Path, any, bool]]
        List of (item, result, success) tuples
    """
    results = []
    completed = 0
    
    print(f"Starting {description} for {len(items)} items with {maxWorkers} workers...")
    
    # Use a lock to coordinate file system access
    processLock = threading.Lock()
    
    def safeProcessItem(item: Path) -> Tuple[Path, any, bool]:
        """Safely process a single item with error handling."""
        nonlocal completed
        
        try:
            # Add small random delay to reduce simultaneous access
            import random
            time.sleep(random.uniform(0.1, 0.3))
            
            # Process the item
            result = processFunc(item)
            
            # Thread-safe logging
            with processLock:
                completed += 1
                print(f"[{completed}/{len(items)}] ✅ {item.name} completed")
                
            return (item, result, True)
            
        except Exception as e:
            with processLock:
                completed += 1
                logger.error(f"[{completed}/{len(items)}] ❌ {item.name} failed: {e}")
                
            return (item, None, False)
    
    # Process in parallel with controlled concurrency
    with concurrent.futures.ThreadPoolExecutor(max_workers=maxWorkers) as executor:
        # Submit all tasks
        futures = {executor.submit(safeProcessItem, item): item for item in items}
        
        # Collect results as they complete
        for future in concurrent.futures.as_completed(futures):
            result = future.result()
            results.append(result)
    
    successCount = sum(1 for _, _, success in results if success)
    print(f"✅ {description} completed: {successCount}/{len(items)} successful")
    
    return results

def processAllMlirBenchmarksParallel(maxWorkers: int = 2) -> list:
    """Process all MLIR benchmarks using parallel processing with race condition prevention.
    
    Parameters
    ---------- 
    maxWorkers : int
        Maximum number of parallel workers (keep low to avoid resource conflicts)

    Returns
    -------
    list
        List of all successfully generated Verilog file paths
    """
    print(f"Starting parallel MLIR pipeline processing with {maxWorkers} workers...")
    
    # Find all MLIR files in the benchmark directory
    mlirFiles = findMlirBenchmarks(BENCHMARK_ROOT_DIR)
    if not mlirFiles:
        logger.warning(f"No MLIR files found in {BENCHMARK_ROOT_DIR}")
        return []
    
    # Create output directories for all processing stages
    VERILOG_OUTPUT_DIR.mkdir(parents=True, exist_ok=True)
    MLIR_OPTIMIZED_DIR.mkdir(parents=True, exist_ok=True)
    MLIR_EXTRACTED_DIR.mkdir(parents=True, exist_ok=True)
    FUTIL_OUTPUT_DIR.mkdir(parents=True, exist_ok=True)
    
    def processOneMlirFile(mlirFile: Path) -> list:
        """Process a single MLIR file through the complete pipeline."""
        try:
            verilogOutputBasePath = VERILOG_OUTPUT_DIR / f"{mlirFile.stem}.sv"
            generatedFiles = mlirPipeline(mlirFile, verilogOutputBasePath)
            return generatedFiles if generatedFiles else []
        except Exception as e:
            logger.error(f"Pipeline failed for {mlirFile.name}: {e}")
            return []
    
    # Process all MLIR files in parallel
    results = processWithSafeParallel(
        mlirFiles,
        processOneMlirFile,
        maxWorkers=maxWorkers,
        description="MLIR Pipeline Processing"
    )
    
    # Collect all generated Verilog files
    allGeneratedVerilog = []
    for mlirFile, verilogFiles, success in results:
        if success and verilogFiles:
            allGeneratedVerilog.extend(verilogFiles)
    
    print(f"\n📊 Parallel MLIR Pipeline Summary:")
    print(f"   📁 Total MLIR files processed: {len(mlirFiles)}")
    print(f"   ✅ Successful conversions: {sum(1 for _, _, success in results if success)}")
    print(f"   ❌ Failed conversions: {sum(1 for _, _, success in results if not success)}")
    print(f"   📝 Total Verilog files generated: {len(allGeneratedVerilog)}")
    

    return allGeneratedVerilog

print("✅ Improved parallel processing with race condition prevention ready")
print("✅ Safe concurrent MLIR pipeline processing available")

✅ Improved parallel processing with race condition prevention ready
✅ Safe concurrent MLIR pipeline processing available


In [11]:
# Execute MLIR Processing Pipeline and Organize Results - Sequential Processing

print("Starting MLIR to Verilog conversion process from unoptimized MLIR files...")
print("Processing will happen sequentially, file by file, for better control and debugging")

# Process MLIR benchmarks from the BENCHMARK folder
print(f"Processing unoptimized MLIR files from: {BENCHMARK_ROOT_DIR}")

# Find available MLIR files
availableMlirFiles = findMlirBenchmarks(BENCHMARK_ROOT_DIR)

if availableMlirFiles:
    print(f"Found {len(availableMlirFiles)} MLIR benchmark files:")
    for mlirFile in availableMlirFiles:
        print(f"  - {mlirFile.name}")
    
    # Process MLIR files sequentially with detailed progress tracking
    print(f"\n🔄 Starting sequential processing of {len(availableMlirFiles)} MLIR files...")
    
    availableVerilogFiles = []
    successfulFiles = 0
    failedFiles = 0
    
    # Create output directories
    VERILOG_OUTPUT_DIR.mkdir(parents=True, exist_ok=True)
    MLIR_OPTIMIZED_DIR.mkdir(parents=True, exist_ok=True)
    MLIR_EXTRACTED_DIR.mkdir(parents=True, exist_ok=True)
    FUTIL_OUTPUT_DIR.mkdir(parents=True, exist_ok=True)
    
    for fileIndex, mlirFile in enumerate(availableMlirFiles, 1):
        print(f"\n📁 [{fileIndex}/{len(availableMlirFiles)}] Processing: {mlirFile.name} ({fileIndex/len(availableMlirFiles)*100:.1f}%)")
        
        try:
            # Process this single MLIR file
            generatedFiles = processBenchmarkMlir(mlirFile, VERILOG_OUTPUT_DIR)
            
            if generatedFiles:
                availableVerilogFiles.extend(generatedFiles)
                successfulFiles += 1
                print(f"   ✅ Success: Generated {len(generatedFiles)} Verilog files")
                # Only log individual files if there are multiple functions per MLIR file
                if len(generatedFiles) > 1:
                    for vFile in generatedFiles:
                        print(f"      📝 {vFile.name}")
                else:
                    print(f"      📝 {generatedFiles[0].name}")
            else:
                failedFiles += 1
                logger.error(f"   ❌ Failed: No Verilog files generated")
                
        except Exception as e:
            failedFiles += 1
            logger.error(f"   💥 Exception: {e}")
            import traceback
            logger.error(f"   📋 Traceback: {traceback.format_exc()}")
        
        # Brief pause between files for system stability
        if fileIndex < len(availableMlirFiles):
            import time
            time.sleep(0.5)  # Small delay between files
    
    # Summary of sequential processing
    print(f"\n📊 Sequential MLIR Processing Summary:")
    print(f"   📁 Total MLIR files processed: {len(availableMlirFiles)}")
    print(f"   ✅ Successful conversions: {successfulFiles}")
    print(f"   ❌ Failed conversions: {failedFiles}")
    print(f"   📝 Total Verilog files generated: {len(availableVerilogFiles)}")
    print(f"   📈 Success rate: {successfulFiles/len(availableMlirFiles)*100:.1f}%")
    
else:
    logger.warning(f"No MLIR files found in {BENCHMARK_ROOT_DIR}")
    # Check if we already have generated Verilog files
    if VERILOG_OUTPUT_DIR.exists():
        availableVerilogFiles = list(VERILOG_OUTPUT_DIR.glob("*.sv"))
        print(f"Found {len(availableVerilogFiles)} existing Verilog files")
    else:
        availableVerilogFiles = []
        logger.warning("No Verilog files found")

# Organize files for processing - group by MLIR source benchmark
print(f"\n🗂️  Organizing generated Verilog files by benchmark source...")
benchmarkStructure = {}

if availableVerilogFiles:
    # Group files by MLIR source for organization
    for vFile in availableVerilogFiles:
        # Extract the base MLIR benchmark name (before any function suffix)
        # Expected format: benchmarkName_functionName.sv
        baseName = vFile.stem
        
        # If there are function suffixes (like _funcName), extract the benchmark name
        if "_" in baseName:
            # Split by underscore and try to identify the benchmark part
            parts = baseName.split("_")
            # Use the first part as the benchmark name, or find a reasonable split
            benchmarkBaseName = parts[0]
            # If we have a pattern like "benchmark_func_name", use first two parts
            if len(parts) > 2 and parts[-1].isdigit():
                benchmarkBaseName = "_".join(parts[:-1])
            elif len(parts) > 1:
                benchmarkBaseName = parts[0]
        else:
            benchmarkBaseName = baseName
        
        if benchmarkBaseName not in benchmarkStructure:
            benchmarkStructure[benchmarkBaseName] = []
        benchmarkStructure[benchmarkBaseName].append(vFile)
    
    # Sort for consistent ordering
    for benchmarkName in benchmarkStructure:
        benchmarkStructure[benchmarkName].sort()

print(f"Generated Verilog files organized into {len(benchmarkStructure)} benchmark groups:")
for groupName, files in benchmarkStructure.items():
    print(f"  📊 {groupName}: {len(files)} files")
    # Only show individual files if there are multiple files per group
    if len(files) <= 3:  # Show individual files only for small groups
        for vFile in files:
            print(f"    📝 {vFile.name}")
    else:
        print(f"    📝 {files[0].name} ... and {len(files)-1} more")

print(f"\n📈 Final Results:")
print(f"   📁 Total available Verilog files: {len(availableVerilogFiles)}")
print(f"   🗂️  Organized into {len(benchmarkStructure)} benchmark groups")

if not availableVerilogFiles:
    logger.warning("❌ No Verilog files were generated from MLIR! Check MLIR files and pipeline availability.")
    print("🔍 Diagnostic information:")
    print(f"   📂 BENCHMARK_ROOT_DIR: {BENCHMARK_ROOT_DIR}")
    print(f"   📂 VERILOG_OUTPUT_DIR: {VERILOG_OUTPUT_DIR}")
    print(f"   📂 Stage directories: {COMPILATION_RESULT_DIR}/01-05_*")
    # Fallback to original source if no generated files exist
    print(f"   🔄 Will use fallback source: {FALLBACK_SOURCE_HDL}")
else:
    print("✅ MLIR to Verilog conversion completed successfully")
    print("🚀 Ready to proceed with parameter sweep using generated Verilog files")

Starting MLIR to Verilog conversion process from unoptimized MLIR files...
Processing will happen sequentially, file by file, for better control and debugging
Processing unoptimized MLIR files from: /home/kelvin/FABulous_fork/myProject/PnR/mlir
Found 13 MLIR files in /home/kelvin/FABulous_fork/myProject/PnR/mlir
  - nw_nw.mlir
  - gemm_ncubed.mlir
  - sort_radix.mlir
  - fft_transpose.mlir
  - kmp_kmp.mlir
  - spmv_crs.mlir
  - gemm_blocked.mlir
  - fft_strided.mlir
  - md_knn.mlir
  - spmv_ellpack.mlir
  - stencil_stencil3d.mlir
  - bfs_queue.mlir
  - stencil_stencil2d.mlir
Found 13 MLIR benchmark files:
  - nw_nw.mlir
  - gemm_ncubed.mlir
  - sort_radix.mlir
  - fft_transpose.mlir
  - kmp_kmp.mlir
  - spmv_crs.mlir
  - gemm_blocked.mlir
  - fft_strided.mlir
  - md_knn.mlir
  - spmv_ellpack.mlir
  - stencil_stencil3d.mlir
  - bfs_queue.mlir
  - stencil_stencil2d.mlir

🔄 Starting sequential processing of 13 MLIR files...

📁 [1/13] Processing: nw_nw.mlir (7.7%)
=== Starting MLIR Pipelin

2025-06-26 13:41:36.455 | ERROR    | __main__:stepMlirToFutil:61 - Error processing function 'nw_nw_inner_loop_0': hlstool failed: /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mlir/nw_nw.mlir:28:12: error: %arg56 != %67#0do-while loops not supported; expected iter-args to remain untransformed in the 'before' region of the scf.while op.
    %0:5 = scf.while (%arg6 = %c0_i32, %arg7 = %c0_i32, %arg8 = %c128_i32, %arg9 = %c128_i32) : (i32, i32, i32, i32) -> (i32, i32, i32, i32, i32) {
           ^
/home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mlir/nw_nw.mlir:28:12: note: see current operation: 
%13:5 = "scf.while"(%2, %2, %4, %4) ({
^bb0(%arg15: i32, %arg16: i32, %arg17: i32, %arg18: i32):
  %20 = "arith.cmpi"(%arg18, %2) <{predicate = 4 : i64}> : (i32, i32) -> i1
  %21 = "scf.if"(%20) ({
    "scf.yield"(%8) : (i1) -> ()
  }, {
    %48 = "arith.cmpi"(%arg17, %2) <{predicate = 4 : i64}> : (i32, i32) -> i1
    "scf.yield"(%48) : (i1) -> 

Processing function 'nw_nw_inner_loop_1' -> nw_nw_inner_loop_1.futil


2025-06-26 13:41:45.327 | ERROR    | __main__:stepMlirToFutil:61 - Error processing function 'nw_nw_inner_loop_1': hlstool failed: /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mlir/nw_nw.mlir:28:12: error: %arg56 != %67#0do-while loops not supported; expected iter-args to remain untransformed in the 'before' region of the scf.while op.
    %0:5 = scf.while (%arg6 = %c0_i32, %arg7 = %c0_i32, %arg8 = %c128_i32, %arg9 = %c128_i32) : (i32, i32, i32, i32) -> (i32, i32, i32, i32, i32) {
           ^
/home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mlir/nw_nw.mlir:28:12: note: see current operation: 
%13:5 = "scf.while"(%2, %2, %4, %4) ({
^bb0(%arg15: i32, %arg16: i32, %arg17: i32, %arg18: i32):
  %20 = "arith.cmpi"(%arg18, %2) <{predicate = 4 : i64}> : (i32, i32) -> i1
  %21 = "scf.if"(%20) ({
    "scf.yield"(%8) : (i1) -> ()
  }, {
    %48 = "arith.cmpi"(%arg17, %2) <{predicate = 4 : i64}> : (i32, i32) -> i1
    "scf.yield"(%48) : (i1) -> 

Processing function 'nw_nw_inner_loop_2' -> nw_nw_inner_loop_2.futil


...


📁 [8/13] Processing: fft_strided.mlir (61.5%)
=== Starting MLIR Pipeline: fft_strided.mlir ===
Step 1: Applying MLIR optimizations: fft_strided.mlir
Applying MLIR optimizations to fft_strided.mlir
Optimizations: int-range, sroa, memref normalization, affine passes
✓ MLIR optimizations completed for fft_strided.mlir
Step 2: Converting inner loops to functions: fft_strided.mlir -> fft_strided.mlir
Read 4165 characters from /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/01_optimized_mlir/fft_strided.mlir
Successfully parsed with xDSL! Module has 1 operations
Found function: fft_strided
  Found 0 innermost loops
Output written to /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mlir/fft_strided.tmp using xDSL
✓ Inner loop conversion and MLIR round trip completed for fft_strided.mlir
Step 3: Converting MLIR to FUTIL: fft_strided.mlir -> multiple FUTIL files
Found functions in fft_strided.mlir: []
Found 0 functions to extract: []
✓ MLIR to FUTIL conversi

2025-06-26 13:42:53.985 | ERROR    | __main__:stepMlirToFutil:61 - Error processing function 'md_knn_inner_loop_0': hlstool failed: hlstool: /home/kelvin/circt/llvm/mlir/lib/IR/PatternMatch.cpp:178: auto mlir::RewriterBase::eraseOp(Operation *)::(anonymous class)::operator()(Operation *) const: Assertion `mayBeGraphRegion(*op->getParentRegion()) && "expected that op has no uses"' failed.
PLEASE submit a bug report to https://github.com/llvm/circt and include the crash backtrace.
Stack dump:
0.	Program arguments: hlstool --calyx-hw --output-level=core --ir --allow-unregistered-dialects --top-level-function=md_knn_inner_loop_0 /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mlir/md_knn.mlir -o /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/03_futil/md_knn_inner_loop_0.mlir
 #0 0x0000747fa138e5f9 llvm::sys::PrintStackTrace(llvm::raw_ostream&, int) /home/kelvin/circt/llvm/llvm/lib/Support/Unix/Signals.inc:804:11
 #1 0x0000747fa138eb2b PrintStackTraceSi

✓ MLIR to FUTIL conversion completed: 0/1 functions successful

📁 [10/13] Processing: spmv_ellpack.mlir (76.9%)
=== Starting MLIR Pipeline: spmv_ellpack.mlir ===
Step 1: Applying MLIR optimizations: spmv_ellpack.mlir
Applying MLIR optimizations to spmv_ellpack.mlir
Optimizations: int-range, sroa, memref normalization, affine passes
✓ MLIR optimizations completed for spmv_ellpack.mlir
Step 2: Converting inner loops to functions: spmv_ellpack.mlir -> spmv_ellpack.mlir
Read 1659 characters from /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/01_optimized_mlir/spmv_ellpack.mlir
Successfully parsed with xDSL! Module has 1 operations
Found function: spmv_ellpack
  Found 1 innermost loops
    Loop 0: affine.for
    External values found: 6, Constants to recreate: 0
  Replaced loop body of affine.for with call to spmv_ellpack_inner_loop_0
Output written to /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mlir/spmv_ellpack.tmp using xDSL
✓ Inner loop conversi

2025-06-26 13:43:09.061 | ERROR    | __main__:stepMlirToFutil:61 - Error processing function 'bfs_queue_inner_loop_0': hlstool failed: hlstool: /home/kelvin/circt/lib/Conversion/SCFToCalyx/SCFToCalyx.cpp:189: void circt::scftocalyx::IfLoweringStateInterface::setResultRegs(scf::IfOp, calyx::RegisterOp, unsigned int): Assertion `idx < op->getNumOperands()' failed.
PLEASE submit a bug report to https://github.com/llvm/circt and include the crash backtrace.
Stack dump:
0.	Program arguments: hlstool --calyx-hw --output-level=core --ir --allow-unregistered-dialects --top-level-function=bfs_queue_inner_loop_0 /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mlir/bfs_queue.mlir -o /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/03_futil/bfs_queue_inner_loop_0.mlir
 #0 0x0000722ce198e5f9 llvm::sys::PrintStackTrace(llvm::raw_ostream&, int) /home/kelvin/circt/llvm/llvm/lib/Support/Unix/Signals.inc:804:11
 #1 0x0000722ce198eb2b PrintStackTraceSignalHandler(void*

✓ MLIR to FUTIL conversion completed: 0/1 functions successful

📁 [13/13] Processing: stencil_stencil2d.mlir (100.0%)
=== Starting MLIR Pipeline: stencil_stencil2d.mlir ===
Step 1: Applying MLIR optimizations: stencil_stencil2d.mlir
Applying MLIR optimizations to stencil_stencil2d.mlir
Optimizations: int-range, sroa, memref normalization, affine passes
✓ MLIR optimizations completed for stencil_stencil2d.mlir
Step 2: Converting inner loops to functions: stencil_stencil2d.mlir -> stencil_stencil2d.mlir
Read 2134 characters from /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/01_optimized_mlir/stencil_stencil2d.mlir
Successfully parsed with xDSL! Module has 1 operations
Found function: stencil_stencil2d
  Found 1 innermost loops
    Loop 0: affine.for
    External values found: 7, Constants to recreate: 0
  Replaced loop body of affine.for with call to stencil_stencil2d_inner_loop_0
Output written to /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/02_extracted_mli

## 3. NextPNR Execution and Analysis Functions

Define functions to run FABulous preprocessing and nextpnr-himbaechel with comprehensive error analysis.

In [ ]:
def run_fabulous_preprocessing(sourceHdlPath: Path) -> bool:
    """
    Run FABulous preprocessing commands to generate necessary files for a specific source HDL.
    Updated to work with generated Verilog files from MLIR processing.
    
    Parameters
    ----------
    sourceHdlPath : Path
        Path to the source HDL file to use for synthesis
    
    Returns
    -------
    bool
        True if successful, False otherwise
    """
    # Ensure the source file exists
    if not sourceHdlPath.exists():
        logger.error(f"Source HDL file does not exist: {sourceHdlPath}")
        return False
        
    # Run FABulous command with the specified source HDL
    fabulousCmd = [
        "FABulous", "--debug", str(FAB_PROJ_DIR), "-p",
        "load_fabric; gen_bitStream_spec; gen_cells_and_techmaps; "
        f"gen_chipdb -routing_graph {FAB_PROJ_DIR}/.FABulous/routing_graph.dot -filter 5,1 5,2 5,3 5,4; "
        f"synthesis_script {sourceHdlPath} -tcl {FAB_PROJ_DIR}/.FABulous/arch_synth.tcl;"
    ]
    
    print(f"Running FABulous preprocessing for: {sourceHdlPath.name}")
    print(f"Command: {' '.join(fabulousCmd)}")
    
    # Set environment for subprocess - generate JSON with proper naming in Verilog directory
    env = os.environ.copy()
    synthJsonPath = VERILOG_OUTPUT_DIR / f"{sourceHdlPath.stem}_synth.json"
    env["OUT_JSON_PATH"] = str(synthJsonPath)

    print("Writing synthesis JSON to: " + str(synthJsonPath))
    
    try:
        result = subprocess.run(fabulousCmd, capture_output=True, text=True, timeout=300, env=env)
        if result.returncode != 0:
            logger.error(f"FABulous preprocessing failed with return code: {result.returncode}")
            logger.error(f"STDOUT: {result.stdout}")
            logger.error(f"STDERR: {result.stderr}")
            return False
        print(result.stdout)
        print(result.stderr)
        # Verify that the JSON file was created
        if not synthJsonPath.exists():
            logger.error(f"Expected synthesis JSON file was not created: {synthJsonPath}")
            return False
        
        print("FABulous preprocessing completed successfully")
        print(f"Generated synthesis JSON: {synthJsonPath}")
        return True
        
    except subprocess.TimeoutExpired:
        logger.error(f"FABulous preprocessing timed out for {sourceHdlPath.name}")
        return False
    except Exception as e:
        logger.error(f"Exception during FABulous preprocessing: {e}")
        return False


2025-06-25T13:51:28.565475+0100 | INFO | Updated helper functions defined successfully with MLIR-based preprocessing
2025-06-25T13:51:28.565887+0100 | INFO | New features: MLIR->Verilog generation, enhanced synthesis failure detection
2025-06-25T13:51:28.565887+0100 | INFO | New features: MLIR->Verilog generation, enhanced synthesis failure detection


In [ ]:

def analyzeNextpnrLogs(stdout: str, stderr: str) -> dict:
    """
    Analyze nextpnr output logs to determine failure types and extract statistics.
    Enhanced to detect synthesis failures from generated Verilog files.
    
    Parameters
    ----------
    stdout : str
        Standard output from nextpnr run
    stderr : str
        Standard error from nextpnr run
    
    Returns
    -------
    dict
        Dictionary containing analysis results:
        - synthesisSuccess: bool - Whether synthesis completed successfully
        - synthesisError: str - Synthesis error message if any
        - placementSuccess: bool - Whether placement completed successfully
        - routingSuccess: bool - Whether routing completed successfully  
        - routingFailed: bool - Whether routing explicitly failed
        - arcQueueSize: int or None - Final arc queue size if found
        - failureType: str - "none", "synthesis", "placement", "routing", or "unknown"
    """
    combinedOutput = stdout + "\n" + stderr
    
    # Initialize results
    result = {
        "synthesisSuccess": False,
        "synthesisError": "none",
        "placementSuccess": False,
        "routingSuccess": False,
        "routingFailed": False,
        "arcQueueSize": None,
        "failureType": "none"
    }
    
    # Check for synthesis errors first (these prevent everything else)
    synthesisErrorPatterns = [
        "Error: Failed to parse JSON file",
        "Error: JSON parsing failed", 
        "Error: Cannot read JSON",
        "Error: Invalid JSON format",
        "Error: Synthesis failed",
        "Error: Yosys synthesis error",
        "Error: Cannot load design",
        "Error: Design elaboration failed",
        "Error: Netlist parsing error",
        "json11: parse error",
        "ERROR: Failed to load JSON",
        "ERROR: Synthesis error",
        "Error: Module not found",
        "Error: Unresolved reference"
    ]
    
    for pattern in synthesisErrorPatterns:
        if pattern.lower() in combinedOutput.lower():
            result["synthesisError"] = pattern
            result["failureType"] = "synthesis"
            return result  # Early return for synthesis errors
    
    # If no synthesis errors found, assume synthesis succeeded
    result["synthesisSuccess"] = True
    
    # Check for placement success - look for "Final Placement" line
    placementSuccess = "Final Placement" in combinedOutput
    result["placementSuccess"] = placementSuccess
    
    # Check for placement failures
    placementFailurePatterns = [
        "ERROR: Unable to place cell",
        "ERROR: Placement failed",
        "Error: Cannot place",
        "Error: Placement error",
        "FATAL: Placement failed",
        "failed to place"
    ]
    
    for pattern in placementFailurePatterns:
        if pattern.lower() in combinedOutput.lower():
            result["placementSuccess"] = False
            result["failureType"] = "placement"
            return result
    
    # Check for routing failure - look for "ERROR: Max iteration count reached"
    routingFailed = "ERROR: Max iteration count reached" in combinedOutput
    result["routingFailed"] = routingFailed
    
    # Extract arc_queue size - look for lines containing "current arc_queue size"
    arcQueueMatches = re.findall(r"current arc_queue size[:\s]*(\d+)", combinedOutput, re.IGNORECASE)
    if arcQueueMatches:
        # Take the last (most recent) arc_queue size found
        result["arcQueueSize"] = int(arcQueueMatches[-1])
    
    # Determine routing success
    # Routing is successful if placement succeeded and routing didn't explicitly fail
    routingSuccess = placementSuccess and not routingFailed
    result["routingSuccess"] = routingSuccess
    
    # Determine failure type
    if result["synthesisSuccess"] and placementSuccess and routingSuccess:
        result["failureType"] = "none"
    elif not result["synthesisSuccess"]:
        result["failureType"] = "synthesis"
    elif not placementSuccess:
        result["failureType"] = "placement"  
    elif placementSuccess and routingFailed:
        result["failureType"] = "routing"
    else:
        result["failureType"] = "unknown"
    
    return result


In [ ]:

def runNextpnrHimbaechel(connectivityFactor: float, congestionFactor: float, sourceFileName: str = "default") -> dict:
    """
    Run nextpnr-himbaechel with specified parameters.
    
    Parameters
    ----------
    connectivityFactor : float
        Placer heap architecture connectivity factor
    congestionFactor : float
        Placer heap congestion aware factor
    sourceFileName : str
        Name of the source file (used for output naming)
    
    Returns
    -------
    dict
        Dictionary containing run results and comprehensive failure analysis
    """
    # Generate unique output filenames with source file name
    timestamp = datetime.now().strftime("%Y%m%d_%H%M%S")
    connStr = f"{connectivityFactor:.1f}".replace(".", "p")
    congStr = f"{congestionFactor:.1f}".replace(".", "p")
    
    # Clean source file name for filename
    cleanSourceName = Path(sourceFileName).stem.replace(".", "_")
    
    outputJson = OUTPUT_DIR / f"{cleanSourceName}_conn{connStr}_cong{congStr}.json"
    outputFasm = OUTPUT_DIR / f"{cleanSourceName}_conn{connStr}_cong{congStr}.fasm"
    
    # Build nextpnr command - use the synthesis JSON generated from the Verilog file
    synthJsonPath = VERILOG_OUTPUT_DIR / f"{Path(sourceFileName).stem}_synth.json"
    
    nextpnrCmd = [
        "nextpnr-himbaechel",
        "--chipdb", str(CHIPDB_PATH),
        "--device", "FABulous",
        "--json", str(synthJsonPath),
        "--write", str(outputJson),
        "-o", f"constrain-pair={CONSTRAIN_PAIR}",
        # "-o", f"fasm={outputFasm}",  # Uncomment if FASM output needed
        "-o", f"fdc={FDC_PATH}",
        "--placer-heap-seed-placement-strategy", "graph_grid",
        "--placer-heap-beta", str(BETA_VALUE),
        "--placer-heap-arch-connectivity-factor", str(connectivityFactor),
        "--placer-heap-congestion-aware-factor", str(congestionFactor),
        "-o", f"placeTrial={PLACE_TRIALS}",
        "--router1-timeout", str(ROUTER_TIMEOUT)
    ]
    
    startTime = time.time()
    
    try:
        print(f"Running nextpnr for {cleanSourceName}: connectivity={connectivityFactor:.1f}, congestion={congestionFactor:.1f}")
        
        # Set environment for subprocess
        env = os.environ.copy()
        result = subprocess.run(nextpnrCmd, capture_output=True, text=True, timeout=600, env=env)
        endTime = time.time()
        runtime = endTime - startTime
        
        success = result.returncode == 0
        
        # Analyze logs for detailed failure information including synthesis
        logAnalysis = analyzeNextpnrLogs(result.stdout, result.stderr)
        
        return {
            "sourceFileName": sourceFileName,
            "connectivityFactor": connectivityFactor,
            "congestionFactor": congestionFactor,
            "success": success,
            "runtime": runtime,
            "returnCode": result.returncode,
            "stdout": result.stdout,
            "stderr": result.stderr,
            "outputJson": str(outputJson) if success else None,
            "outputFasm": str(outputFasm) if success else None,
            "timestamp": timestamp,
            # Add detailed failure analysis including synthesis
            "synthesisSuccess": logAnalysis["synthesisSuccess"],
            "synthesisError": logAnalysis["synthesisError"],
            "placementSuccess": logAnalysis["placementSuccess"],
            "routingSuccess": logAnalysis["routingSuccess"], 
            "routingFailed": logAnalysis["routingFailed"],
            "arcQueueSize": logAnalysis["arcQueueSize"],
            "failureType": logAnalysis["failureType"]
        }
        
    except subprocess.TimeoutExpired:
        endTime = time.time()
        runtime = endTime - startTime
        logger.warning(f"nextpnr timed out for {cleanSourceName}: connectivity={connectivityFactor:.1f}, congestion={congestionFactor:.1f}")
        
        return {
            "sourceFileName": sourceFileName,
            "connectivityFactor": connectivityFactor,
            "congestionFactor": congestionFactor,
            "success": False,
            "runtime": runtime,
            "returnCode": -1,
            "stdout": "",
            "stderr": "Timeout",
            "outputJson": None,
            "outputFasm": None,
            "timestamp": timestamp,
            # Add failure analysis fields for timeout case
            "synthesisSuccess": False,
            "synthesisError": "Timeout",
            "placementSuccess": False,
            "routingSuccess": False,
            "routingFailed": False,
            "arcQueueSize": None,
            "failureType": "timeout"
        }
    except Exception as e:
        endTime = time.time()
        runtime = endTime - startTime
        logger.error(f"Error running nextpnr for {cleanSourceName}: {e}")
        
        return {
            "sourceFileName": sourceFileName,
            "connectivityFactor": connectivityFactor,
            "congestionFactor": congestionFactor,
            "success": False,
            "runtime": runtime,
            "returnCode": -2,
            "stdout": "",
            "stderr": str(e),
            "outputJson": None,
            "outputFasm": None,
            "timestamp": timestamp,
            # Add failure analysis fields for exception case
            "synthesisSuccess": False,
            "synthesisError": f"Exception: {str(e)}",
            "placementSuccess": False,
            "routingSuccess": False,
            "routingFailed": False,
            "arcQueueSize": None,
            "failureType": "exception"
        }

def runParameterSweepForSource(sourceHdlPath: Path) -> list[dict]:
    """
    Run parameter sweep for a specific source HDL file.
    
    Parameters
    ----------
    sourceHdlPath : Path
        Path to the source HDL file
        
    Returns
    -------
    list[dict]
        List of results for all parameter combinations
    """
    print(f"Starting parameter sweep for: {sourceHdlPath.name}")
    
    # Run preprocessing for this source file
    if not run_fabulous_preprocessing(sourceHdlPath):
        logger.error(f"Preprocessing failed for {sourceHdlPath.name}. Skipping parameter sweep.")
        return []
    
    # Run parameter combinations
    results = []
    totalCombinations = len(grid)
    
    print(f"Running {totalCombinations} parameter combinations for {sourceHdlPath.name}")
    
    def runAndLog(args: tuple) -> dict:
        connectivityFactor, congestionFactor = args
        result = runNextpnrHimbaechel(connectivityFactor, congestionFactor, sourceHdlPath.name)
        if result["success"]:
            print(f"✓ {sourceHdlPath.name}: conn={connectivityFactor:.1f}, cong={congestionFactor:.1f} completed in {result['runtime']:.2f}s")
        else:
            failureInfo = ""
            if 'failureType' in result:
                failureInfo = f" ({result['failureType']})"
                if result['failureType'] == 'synthesis' and result.get('synthesisError') != 'none':
                    failureInfo += f" - {result['synthesisError']}"
                elif result.get('arcQueueSize') is not None:
                    failureInfo += f" [arc_queue: {result['arcQueueSize']}]"
            logger.warning(f"✗ {sourceHdlPath.name}: conn={connectivityFactor:.1f}, cong={congestionFactor:.1f} failed with code {result['returnCode']}{failureInfo}")
        return result

    # Use reduced concurrency to avoid overwhelming the system
    maxWorkers = min(16, os.cpu_count() or 2)  # Reduced for stability with MLIR processing
    
    with concurrent.futures.ThreadPoolExecutor(max_workers=maxWorkers) as executor:
        futures = [executor.submit(runAndLog, args) for args in grid]
        for future in concurrent.futures.as_completed(futures):
            results.append(future.result())
    
    successCount = sum(1 for r in results if r['success'])
    synthesisSuccessCount = sum(1 for r in results if r.get('synthesisSuccess', False))
    
    print(f"Parameter sweep completed for {sourceHdlPath.name}:")  
    print(f"  Synthesis: {synthesisSuccessCount}/{len(results)} successful")
    print(f"  Overall: {successCount}/{len(results)} successful")
    
    return results

print("Updated helper functions defined successfully with MLIR-based preprocessing")
print("New features: MLIR->Verilog generation, enhanced synthesis failure detection")

In [11]:
sourceResults = runParameterSweepForSource(Path("/home/kelvin/FABulous_fork/myProject/PnR/mlir_trail/mlir_trail_test_bfs_queue_inner_loop_0.sv"))

2025-06-25T13:51:46.892928+0100 | INFO | Starting parameter sweep for: mlir_trail_test_bfs_queue_inner_loop_0.sv
2025-06-25T13:51:46.893338+0100 | INFO | Running FABulous preprocessing for: mlir_trail_test_bfs_queue_inner_loop_0.sv
2025-06-25T13:51:46.893555+0100 | INFO | Command: FABulous --debug /home/kelvin/FABulous_fork/myProject -p load_fabric; gen_bitStream_spec; gen_cells_and_techmaps; gen_chipdb -routing_graph /home/kelvin/FABulous_fork/myProject/.FABulous/routing_graph.dot -filter 5,1 5,2 5,3 5,4; synthesis_script /home/kelvin/FABulous_fork/myProject/PnR/mlir_trail/mlir_trail_test_bfs_queue_inner_loop_0.sv -tcl /home/kelvin/FABulous_fork/myProject/.FABulous/arch_synth.tcl;
2025-06-25T13:51:46.893803+0100 | INFO | Writing synthesis JSON to: /home/kelvin/FABulous_fork/myProject/PnR/compilation_result/verilog/mlir_trail_test_bfs_queue_inner_loop_0_synth.json
2025-06-25T13:51:46.893338+0100 | INFO | Running FABulous preprocessing for: mlir_trail_test_bfs_queue_inner_loop_0.sv
2025

In [ ]:
# Benchmark Selection Configuration
# Leave empty to process all benchmarks, or specify a list of benchmark names to process only those

# Examples:
# selectedBenchmarks = []  # Process all benchmarks (default)
# selectedBenchmarks = ["aes_aes", "bfs_bulk"]  # Process only these benchmarks
# selectedBenchmarks = [name for name in benchmarkStructure.keys() if "fft" in name]  # Filter by name pattern

selectedBenchmarks = []  # Default: process all benchmarks

# Apply benchmark selection filter
if selectedBenchmarks:
    print(f"Filtering to {len(selectedBenchmarks)} selected benchmarks:")
    filteredBenchmarkStructure = {}
    filteredVerilogFiles = []
    
    for benchmarkName in selectedBenchmarks:
        if benchmarkName in benchmarkStructure:
            filteredBenchmarkStructure[benchmarkName] = benchmarkStructure[benchmarkName]
            filteredVerilogFiles.extend(benchmarkStructure[benchmarkName])
            print(f"  - {benchmarkName}: {len(benchmarkStructure[benchmarkName])} files")
        else:
            logger.warning(f"  - {benchmarkName}: NOT FOUND")
    
    # Update the structures to use
    benchmarkStructure = filteredBenchmarkStructure  
    availableVerilogFiles = filteredVerilogFiles
    
    if not filteredVerilogFiles:
        logger.warning("No files matched the selection criteria!")
else:
    print(f"Will process all {len(benchmarkStructure)} benchmarks with {len(availableVerilogFiles)} total files")

# Final check
if not availableVerilogFiles:
    logger.warning("No Verilog files available for processing!")
    if VERILOG_OUTPUT_DIR.exists():
        print(f"Contents of {VERILOG_OUTPUT_DIR}:")
        for item in VERILOG_OUTPUT_DIR.iterdir():
            print(f"  - {item.name}")
    else:
        logger.error(f"Directory {VERILOG_OUTPUT_DIR} does not exist!")
        
print(f"Final selection: {len(benchmarkStructure)} benchmarks, {len(availableVerilogFiles)} files to process")

2025-06-24T22:15:40.077384+0100 | INFO | Will process all 12 benchmarks with 12 total files
2025-06-24T22:15:40.077902+0100 | INFO | Final selection: 12 benchmarks, 12 files to process


In [ ]:
# Run parameter sweep organized by benchmark
# Each MLIR-generated benchmark will be processed separately for better organization and analysis

allResults = []
benchmarkResults = {}  # Dictionary to store results per benchmark

print(f"Running parameter sweep for {len(benchmarkStructure)} MLIR-derived benchmarks with {len(availableVerilogFiles)} total files...")
print("Each file will undergo its own preprocessing before parameter sweep")

# Process benchmarks individually for better organization
for benchmarkName, benchmarkFiles in benchmarkStructure.items():
    print(f"\n=== Processing MLIR Benchmark: {benchmarkName} ===")
    print(f"Verilog files generated from MLIR: {len(benchmarkFiles)}")
    
    benchmarkSpecificResults = []
    
    for verilogFile in benchmarkFiles:
        print(f"Processing {verilogFile.relative_to(VERILOG_OUTPUT_DIR)}...")
        sourceResults = runParameterSweepForSource(verilogFile)
        
        # Add benchmark information to each result
        for result in sourceResults:
            result["benchmarkName"] = benchmarkName
            result["mlirSource"] = benchmarkName  # Track original MLIR source
            # Extract function name from filename if present
            if benchmarkName in verilogFile.stem:
                functionPart = verilogFile.stem.replace(benchmarkName, "").lstrip("_")
                result["functionName"] = functionPart if functionPart else "main"
            else:
                result["functionName"] = verilogFile.stem
        
        benchmarkSpecificResults.extend(sourceResults)
        allResults.extend(sourceResults)
        
        # Brief pause between files to avoid system overload
        if len(benchmarkFiles) > 1:
            time.sleep(1)
    
    # Store results for this benchmark
    benchmarkResults[benchmarkName] = benchmarkSpecificResults
    
    # Log benchmark summary with division by zero protection
    successfulInBenchmark = sum(1 for r in benchmarkSpecificResults if r["success"])
    totalInBenchmark = len(benchmarkSpecificResults)
    synthesisSuccessfulInBenchmark = sum(1 for r in benchmarkSpecificResults if r.get("synthesisSuccess", False))
    
    print(f"MLIR Benchmark {benchmarkName} completed:")
    if totalInBenchmark > 0:
        print(f"  Synthesis: {synthesisSuccessfulInBenchmark}/{totalInBenchmark} successful ({synthesisSuccessfulInBenchmark/totalInBenchmark*100:.1f}%)")
        print(f"  Overall: {successfulInBenchmark}/{totalInBenchmark} successful ({successfulInBenchmark/totalInBenchmark*100:.1f}%)")
    else:
        print(f"  No results to report (0 parameter combinations)")
    
    # Brief pause between benchmarks
    if len(benchmarkStructure) > 1:
        time.sleep(2)

print("\n=== Overall Summary ===")
print(f"Completed parameter sweep for {len(benchmarkStructure)} MLIR-derived benchmarks")
print(f"Total results collected: {len(allResults)}")

# Per-benchmark summary with division by zero protection
for benchmarkName, results in benchmarkResults.items():
    successful = sum(1 for r in results if r["success"])
    synthesisSuccessful = sum(1 for r in results if r.get("synthesisSuccess", False))
    total = len(results)
    if total > 0:
        print(f"  {benchmarkName}: synthesis {synthesisSuccessful}/{total} ({synthesisSuccessful/total*100:.1f}%), overall {successful}/{total} ({successful/total*100:.1f}%)")
    else:
        print(f"  {benchmarkName}: No results (0 parameter combinations)")

# Create DataFrame for analysis
if allResults:
    df = pd.DataFrame(allResults)
    print(f"DataFrame created with {len(df)} rows and {len(df.columns)} columns")
    print(f"Available columns: {list(df.columns)}")
else:
    df = pd.DataFrame()
    logger.warning("No results available for DataFrame creation")

# Final summary with division by zero protection
totalRuns = len(allResults)
if totalRuns > 0:
    successfulRuns = sum(1 for result in allResults if result["success"])
    synthesisSuccessfulRuns = sum(1 for result in allResults if result.get("synthesisSuccess", False))
    
    print(f"\n🎯 MLIR-based parameter sweep completed!")
    print(f"Total runs: {totalRuns}")
    print(f"Synthesis successful: {synthesisSuccessfulRuns}/{totalRuns} ({synthesisSuccessfulRuns/totalRuns*100:.1f}%)")
    print(f"Overall successful: {successfulRuns}/{totalRuns} ({successfulRuns/totalRuns*100:.1f}%)")
else:
    logger.error("No parameter sweep results available!")
    print("This may be because:")
    print("  - No MLIR files were found in the benchmark directory")
    print("  - No Verilog files were generated from MLIR processing") 
    print("  - All preprocessing steps failed")
    print(f"Check the contents of: {BENCHMARK_ROOT_DIR} and {VERILOG_OUTPUT_DIR}")

2025-06-24T22:15:40.090153+0100 | INFO | Running parameter sweep for 12 benchmarks with 12 total files...
2025-06-24T22:15:40.090528+0100 | INFO | Each file will undergo its own preprocessing before parameter sweep
2025-06-24T22:15:40.090926+0100 | INFO | 
=== Processing Benchmark: cap ===
2025-06-24T22:15:40.091094+0100 | INFO | Files in this benchmark: 1
2025-06-24T22:15:40.091387+0100 | INFO | Processing cap.v...
2025-06-24T22:15:40.091700+0100 | INFO | Starting parameter sweep for: cap.v
2025-06-24T22:15:40.091861+0100 | INFO | Running FABulous preprocessing for: cap.v
2025-06-24T22:15:40.092032+0100 | INFO | Command: FABulous --debug /home/kelvin/FABulous_fork/myProject -p load_fabric; gen_bitStream_spec; gen_cells_and_techmaps; gen_chipdb -routing_graph /home/kelvin/FABulous_fork/myProject/.FABulous/routing_graph.dot -filter 5,1 5,2 5,3 5,4; synthesis_script /home/kelvin/FABulous_fork/myProject/PnR/generated_verilog/cap.v -tcl /home/kelvin/FABulous_fork/myProject/.FABulous/arch_s

ZeroDivisionError: division by zero

## 5. Collect and Display Results - Per Benchmark Analysis

Aggregate the results into a pandas DataFrame and analyze the outcomes both overall and per benchmark.

### Analysis Features:
- **Overall Statistics**: Combined results across all benchmarks
- **Per-Benchmark Analysis**: Individual benchmark performance analysis
- **Loop-Level Details**: Performance breakdown by Loop directories within benchmarks
- **Parameter Sensitivity**: Which parameter combinations work best for each benchmark type
- **Comparative Analysis**: Cross-benchmark performance comparisons

## 6. Interactive Dashboard

Interactive dashboard for exploring parameter sweep results with comprehensive analysis capabilities.

The dashboard provides an intuitive interface for:
- Viewing results across different benchmarks or files
- Analyzing success rates with parameter heatmaps
- Exploring failure patterns and error types
- Examining runtime performance data
- Drilling down into specific parameter combinations

**Key Features:**
- 📊 Summary statistics for overall performance
- 🔥 Success rate heatmaps by parameter combinations  
- ⏱️ Runtime analysis for successful runs
- 🔍 Failure analysis with detailed error breakdown
- 📈 Parameter sensitivity charts
- 📋 Detailed data tables for investigation

The dashboard automatically adapts to your data structure, whether you have multiple benchmarks, source files, or a single unified dataset.

## 7. Interactive Dashboard

Interactive dashboard for exploring results across different Verilog files with combined analysis and file-specific views.

In [ ]:
# Interactive Dashboard for Parameter Sweep Results
try:
    import ipywidgets as widgets
    from IPython.display import display, clear_output
    import matplotlib.pyplot as plt
    import seaborn as sns
    import pandas as pd
    from pathlib import Path
    
    def createInteractiveDashboard(dataFrame: pd.DataFrame) -> None:
        """
        Create an interactive dashboard for exploring parameter sweep results.
        
        Parameters
        ----------
        dataFrame : pd.DataFrame
            DataFrame containing the results to analyze
        """
        
        if len(dataFrame) == 0:
            print("No data available for dashboard. Please run the parameter sweep first.")
            return
        
        print("Creating interactive dashboard...")
        
        # Prepare data
        dfDashboard = dataFrame.copy()
        dfDashboard["connectivityFactor"] = dfDashboard["connectivityFactor"].round(2)
        dfDashboard["congestionFactor"] = dfDashboard["congestionFactor"].round(2)
        
        # Determine available grouping options
        fileOptions = ["All Data (Combined)"]
        groupingCol = None
        
        # Check for benchmark structure
        if 'benchmarkName' in dfDashboard.columns and dfDashboard['benchmarkName'].nunique() > 1:
            groupingCol = 'benchmarkName'
            fileOptions.extend([f"Benchmark: {name}" for name in sorted(dfDashboard['benchmarkName'].unique())])
        # Check for multiple source files
        elif 'sourceFileName' in dfDashboard.columns and dfDashboard['sourceFileName'].nunique() > 1:
            groupingCol = 'sourceFileName'
            fileOptions.extend([f"File: {Path(name).stem}" for name in sorted(dfDashboard['sourceFileName'].unique())])
        
        # Create widgets
        fileSelector = widgets.Dropdown(
            options=fileOptions,
            value="All Data (Combined)",
            description="Select Group:",
            style={"description_width": "initial"}
        )
        
        vizOptions = [
            "Summary Statistics",
            "Success Rate Heatmap",
            "Runtime Heatmap",
            "Failure Analysis",
            "Parameter Sensitivity",
            "Detailed Data Table"
        ]
        
        vizSelector = widgets.Dropdown(
            options=vizOptions,
            value="Summary Statistics",
            description="View Type:",
            style={"description_width": "initial"}
        )
        
        # Output widget for displaying results
        outputWidget = widgets.Output()
        
        def updateDashboard(change=None):
            """Update the dashboard based on current selections"""
            with outputWidget:
                clear_output(wait=True)
                
                selectedFile = fileSelector.value
                selectedViz = vizSelector.value
                
                # Filter data based on selection
                if selectedFile == "All Data (Combined)":
                    filteredData = dfDashboard.copy()
                    titlePrefix = "All Data Combined"
                else:
                    # Parse the selection to get the actual value
                    if selectedFile.startswith("Benchmark: "):
                        groupValue = selectedFile.replace("Benchmark: ", "")
                        filteredData = dfDashboard[dfDashboard['benchmarkName'] == groupValue].copy()
                        titlePrefix = f"Benchmark: {groupValue}"
                    elif selectedFile.startswith("File: "):
                        displayName = selectedFile.replace("File: ", "")
                        # Find the actual filename that matches this display name
                        actualFileName = None
                        for fileName in dfDashboard['sourceFileName'].unique():
                            if Path(fileName).stem == displayName:
                                actualFileName = fileName
                                break
                        if actualFileName:
                            filteredData = dfDashboard[dfDashboard['sourceFileName'] == actualFileName].copy()
                            titlePrefix = f"File: {displayName}"
                        else:
                            print(f"Could not find file matching: {displayName}")
                            return
                    else:
                        filteredData = dfDashboard.copy()
                        titlePrefix = "Unknown Selection"
                
                if len(filteredData) == 0:
                    print(f"No data available for {selectedFile}")
                    return
                
                # Display selected visualization
                try:
                    if selectedViz == "Summary Statistics":
                        displaySummaryStats(filteredData, titlePrefix)
                    elif selectedViz == "Success Rate Heatmap":
                        displaySuccessHeatmap(filteredData, titlePrefix)
                    elif selectedViz == "Runtime Heatmap":
                        displayRuntimeHeatmap(filteredData, titlePrefix)
                    elif selectedViz == "Failure Analysis":
                        displayFailureAnalysis(filteredData, titlePrefix)
                    elif selectedViz == "Parameter Sensitivity":
                        displayParameterSensitivity(filteredData, titlePrefix)
                    elif selectedViz == "Detailed Data Table":
                        displayDataTable(filteredData, titlePrefix)
                except Exception as e:
                    print(f"Error displaying {selectedViz}: {e}")
        
        def displaySummaryStats(data, titlePrefix):
            """Display summary statistics"""
            print(f"=== {titlePrefix} - Summary Statistics ===\n")
            
            successCount = data["success"].sum()
            totalCount = len(data)
            successRate = (successCount / totalCount * 100) if totalCount > 0 else 0
            
            print(f"📊 Total Runs: {totalCount}")
            print(f"✅ Successful Runs: {successCount}")
            print(f"📈 Success Rate: {successRate:.1f}%")
            
            if successCount > 0:
                avgRuntime = data[data["success"]]["runtime"].mean()
                print(f"⏱️ Average Runtime (successful): {avgRuntime:.2f}s")
            
            # Stage-by-stage success rates
            if "synthesisSuccess" in data.columns:
                synthesisRate = data["synthesisSuccess"].mean() * 100
                print(f"\n--- Stage Success Rates ---")
                print(f"🔧 Synthesis: {synthesisRate:.1f}%")
                
                if "placementSuccess" in data.columns:
                    placementRate = data["placementSuccess"].mean() * 100
                    print(f"📍 Placement: {placementRate:.1f}%")
                    
                if "routingSuccess" in data.columns:
                    routingRate = data["routingSuccess"].mean() * 100
                    print(f"🔀 Routing: {routingRate:.1f}%")
            
            # Failure breakdown if available
            if "failureType" in data.columns:
                print(f"\n--- Failure Analysis ---")
                failureCounts = data["failureType"].value_counts()
                for failureType, count in failureCounts.items():
                    if failureType != "none":
                        percentage = (count / totalCount) * 100
                        emoji = "🔧" if failureType == "synthesis" else "📍" if failureType == "placement" else "🔀" if failureType == "routing" else "❓"
                        print(f"{emoji} {failureType.title()} Failures: {count} ({percentage:.1f}%)")
                
                # Show synthesis error details if available
                if "synthesisError" in data.columns:
                    synthesisFailures = data[data["failureType"] == "synthesis"]
                    if len(synthesisFailures) > 0:
                        print(f"\n--- Common Synthesis Errors ---")
                        errorCounts = synthesisFailures["synthesisError"].value_counts().head(3)
                        for error, count in errorCounts.items():
                            if error and str(error) != "nan":
                                shortError = str(error)[:60] + "..." if len(str(error)) > 60 else str(error)
                                print(f"   {count}x: {shortError}")
            
            # Parameter performance
            print(f"\n--- Parameter Performance ---")
            if len(data) > 1:
                connSuccess = data.groupby("connectivityFactor")["success"].mean()
                congSuccess = data.groupby("congestionFactor")["success"].mean()
                
                if len(connSuccess) > 0:
                    bestConn = connSuccess.idxmax()
                    print(f"🎯 Best Connectivity Factor: {bestConn} ({connSuccess[bestConn]*100:.1f}% success)")
                if len(congSuccess) > 0:
                    bestCong = congSuccess.idxmax()
                    print(f"🎯 Best Congestion Factor: {bestCong} ({congSuccess[bestCong]*100:.1f}% success)")
            
            # Arc queue statistics if available
            if "arcQueueSize" in data.columns:
                arcSizes = data["arcQueueSize"].dropna()
                if len(arcSizes) > 0:
                    print(f"\n--- Arc Queue Statistics ---")
                    print(f"📏 Average Arc Queue Size: {arcSizes.mean():.1f}")
                    print(f"📏 Arc Queue Range: {arcSizes.min()} - {arcSizes.max()}")
        
        def displaySuccessHeatmap(data, titlePrefix):
            """Display success rate heatmap"""
            if len(data) <= 1:
                print(f"Not enough data for heatmap visualization")
                return
                
            plt.figure(figsize=(10, 6))
            
            try:
                successPivot = data.pivot_table(
                    values="success",
                    index="connectivityFactor",
                    columns="congestionFactor",
                    aggfunc="mean"
                )
                
                if not successPivot.empty:
                    sns.heatmap(successPivot, annot=True, fmt=".2f", cmap="RdYlGn",
                               vmin=0, vmax=1, cbar_kws={"label": "Success Rate"})
                    plt.title(f"{titlePrefix} - Success Rate Heatmap")
                    plt.ylabel("Connectivity Factor")
                    plt.xlabel("Congestion Factor")
                    plt.tight_layout()
                    plt.show()
                else:
                    print("No data available for success heatmap")
            except Exception as e:
                print(f"Error creating success heatmap: {e}")
        
        def displayRuntimeHeatmap(data, titlePrefix):
            """Display runtime heatmap"""
            successfulData = data[data["success"]]
            
            if len(successfulData) <= 1:
                print(f"Not enough successful runs for runtime heatmap")
                return
                
            plt.figure(figsize=(10, 6))
            
            try:
                runtimePivot = successfulData.pivot_table(
                    values="runtime",
                    index="connectivityFactor",
                    columns="congestionFactor",
                    aggfunc="mean"
                )
                
                if not runtimePivot.empty:
                    sns.heatmap(runtimePivot, annot=True, fmt=".2f", cmap="viridis",
                               cbar_kws={"label": "Runtime (seconds)"})
                    plt.title(f"{titlePrefix} - Runtime Heatmap (Successful Runs)")
                    plt.ylabel("Connectivity Factor")
                    plt.xlabel("Congestion Factor")
                    plt.tight_layout()
                    plt.show()
                else:
                    print("No successful runs available for runtime heatmap")
            except Exception as e:
                print(f"Error creating runtime heatmap: {e}")
        
        def displayFailureAnalysis(data, titlePrefix):
            """Display failure analysis charts"""
            if "failureType" not in data.columns:
                print("Failure type data not available")
                return
                
            plt.figure(figsize=(15, 10))
            
            try:
                # Failure type distribution
                plt.subplot(2, 3, 1)
                failureCounts = data["failureType"].value_counts()
                failureOnly = failureCounts[failureCounts.index != "none"]
                
                if len(failureOnly) > 0:
                    colors = ["#e74c3c", "#f39c12", "#9b59b6"]
                    labels = []
                    for failureType in failureOnly.index:
                        if failureType == "synthesis":
                            labels.append("Synthesis Fail")
                        elif failureType == "placement":
                            labels.append("Placement Fail")
                        elif failureType == "routing":
                            labels.append("Routing Fail")
                        else:
                            labels.append(failureType.title())
                    
                    plt.pie(failureOnly.values, labels=labels, autopct="%1.1f%%",
                           colors=colors[:len(failureOnly)])
                    plt.title("Failure Type Distribution")
                
                # Success rates comparison
                plt.subplot(2, 3, 2)
                successRates = {"Overall": data["success"].mean() * 100}
                
                if "synthesisSuccess" in data.columns:
                    successRates["Synthesis"] = data["synthesisSuccess"].mean() * 100
                if "placementSuccess" in data.columns:
                    successRates["Placement"] = data["placementSuccess"].mean() * 100
                if "routingSuccess" in data.columns and "placementSuccess" in data.columns:
                    routingData = data[data["placementSuccess"]]
                    if len(routingData) > 0:
                        successRates["Routing"] = routingData["routingSuccess"].mean() * 100
                
                bars = plt.bar(successRates.keys(), successRates.values(),
                              color=["#3498db", "#9b59b6", "#2ecc71", "#e67e22"])
                plt.ylabel("Success Rate (%)")
                plt.title("Success Rates by Stage")
                plt.ylim(0, 100)
                
                # Add value labels
                for bar, value in zip(bars, successRates.values()):
                    plt.text(bar.get_x() + bar.get_width()/2, bar.get_height() + 1,
                            f"{value:.1f}%", ha="center", va="bottom")
                
                plt.suptitle(f"{titlePrefix} - Failure Analysis", fontsize=16, fontweight="bold")
                plt.tight_layout()
                plt.show()
                
            except Exception as e:
                print(f"Error creating failure analysis: {e}")
        
        def displayParameterSensitivity(data, titlePrefix):
            """Display parameter sensitivity analysis"""
            if len(data) <= 1:
                print("Not enough data for parameter sensitivity analysis")
                return
                
            plt.figure(figsize=(12, 8))
            
            try:
                # Success rate by parameter values
                plt.subplot(2, 2, 1)
                connSuccess = data.groupby("connectivityFactor")["success"].mean()
                congSuccess = data.groupby("congestionFactor")["success"].mean()
                
                plt.plot(connSuccess.index, connSuccess.values * 100, "o-",
                        label="Connectivity Factor", linewidth=2, markersize=8)
                plt.plot(congSuccess.index, congSuccess.values * 100, "s-",
                        label="Congestion Factor", linewidth=2, markersize=8)
                plt.xlabel("Parameter Value")
                plt.ylabel("Success Rate (%)")
                plt.title("Success Rate by Parameter")
                plt.legend()
                plt.grid(True, alpha=0.3)
                plt.ylim(0, 100)
                
                plt.suptitle(f"{titlePrefix} - Parameter Sensitivity Analysis", fontsize=16, fontweight="bold")
                plt.tight_layout()
                plt.show()
                
            except Exception as e:
                print(f"Error creating parameter sensitivity analysis: {e}")
        
        def displayDataTable(data, titlePrefix):
            """Display detailed data table"""
            print(f"=== {titlePrefix} - Detailed Data Table ===\n")
            
            # Select key columns for display
            displayCols = ["connectivityFactor", "congestionFactor", "success", "runtime"]
            
            if "failureType" in data.columns:
                displayCols.append("failureType")
            if "placementSuccess" in data.columns:
                displayCols.append("placementSuccess")
            if "routingSuccess" in data.columns:
                displayCols.append("routingSuccess")
            if "arcQueueSize" in data.columns:
                displayCols.append("arcQueueSize")
            
            # Filter to existing columns
            availableCols = [col for col in displayCols if col in data.columns]
            
            # Display sample data
            print(f"Showing first 20 rows (Total: {len(data)} rows)\n")
            sampleData = data[availableCols].head(20).copy()
            
            # Format the data for better display
            if "runtime" in sampleData.columns:
                sampleData["runtime"] = sampleData["runtime"].round(2)
            if "arcQueueSize" in sampleData.columns:
                sampleData["arcQueueSize"] = sampleData["arcQueueSize"].fillna(0).astype(int)
            
            print(sampleData.to_string(index=False))
            
            # Show summary statistics
            print(f"\n--- Summary Statistics ---")
            print(f"Total Rows: {len(data)}")
            print(f"Unique Parameter Combinations: {len(data.groupby(['connectivityFactor', 'congestionFactor']))}")
        
        # Set up interactive callbacks
        fileSelector.observe(updateDashboard, names="value")
        vizSelector.observe(updateDashboard, names="value")
        
        # Display the dashboard
        print("=== Interactive Parameter Sweep Dashboard ===\n")
        
        # Show overall statistics
        totalRuns = len(dfDashboard)
        successfulRuns = dfDashboard["success"].sum()
        successRate = (successfulRuns / totalRuns * 100) if totalRuns > 0 else 0
        
        print("📊 Overall Statistics:")
        print(f"   Total Runs: {totalRuns}")
        print(f"   Successful Runs: {successfulRuns}")
        print(f"   Success Rate: {successRate:.1f}%")
        
        if groupingCol:
            groupType = "Benchmarks" if "benchmark" in groupingCol.lower() else "Files"
            uniqueGroups = dfDashboard[groupingCol].nunique()
            print(f"   Unique {groupType}: {uniqueGroups}")
        
        if successfulRuns > 0:
            avgRuntime = dfDashboard[dfDashboard["success"]]["runtime"].mean()
            print(f"   Average Runtime: {avgRuntime:.2f}s")
        print()
        
        # Display the interactive controls
        controlsBox = widgets.HBox([fileSelector, vizSelector])
        display(controlsBox)
        display(outputWidget)
        
        # Initialize with default view
        updateDashboard()
        
        print("Interactive dashboard created successfully!")
    
    # Create the dashboard
    if len(df) > 0:
        createInteractiveDashboard(df)
    else:
        print("No data available for dashboard. Please run the parameter sweep first.")
        
except ImportError as e:
    print(f"Required packages not available for interactive dashboard: {e}")
    print("To enable the interactive dashboard, install:")
    print("pip install ipywidgets")
    print("And enable the extension:")
    print("jupyter nbextension enable --py widgetsnbextension")
    
except Exception as e:
    print(f"Error creating interactive dashboard: {e}")
    import traceback
    traceback.print_exc()

# Final Summary
print("\n" + "="*50)
print("🎯 PARAMETER SWEEP COMPLETE!")
print("="*50)
print(f"Total parameter combinations tested: {len(df)}")
print(f"Successful runs: {df['success'].sum()}")
print(f"Success rate: {df['success'].mean()*100:.1f}%")
print(f"Results directory: {OUTPUT_DIR}")

# Show synthesis results if available
if 'synthesisSuccess' in df.columns:
    synthesisSuccessCount = df['synthesisSuccess'].sum()
    synthesisRate = synthesisSuccessCount / len(df) * 100
    print(f"Synthesis success: {synthesisSuccessCount}/{len(df)} ({synthesisRate:.1f}%)")

print("="*50)

print("✅ Parameter sweep with interactive dashboard completed successfully!")
print(f"Generated comprehensive results with {len(df)} total runs")
print(f"Results saved to: {OUTPUT_DIR}")

print("\n🎉 Interactive dashboard ready for exploration!")

2025-06-20T18:14:19.876996+0100 | INFO | Creating unified interactive dashboard...
=== Unified Interactive Parameter Sweep Dashboard ===

📊 Combined Statistics:
   Total Runs: 432
   Successful Runs: 432
   Success Rate: 100.0%
   Unique Benchmarks: 18
   Avg Runtime: 0.04s



Output()

2025-06-20T18:14:19.882295+0100 | INFO | Unified interactive dashboard created successfully!


## 🎯 Summary: MLIR-Based Pipeline with Synthesis Error Measurement

This notebook now provides a comprehensive **MLIR-to-Verilog parameter sweep pipeline** that starts with unoptimized MLIR files from the BENCHMARK folder and measures synthesis errors as a critical metric.

### 🔧 Pipeline Architecture - MLIR Starting Point

The enhanced pipeline now processes benchmarks through a streamlined workflow:

#### **1. MLIR Input Processing**
- **Benchmark Discovery**: Automatically finds all `.mlir` files in the BENCHMARK folder
- **Unoptimized MLIR**: Starts with raw, unoptimized MLIR files as input
- **Multiple Functions**: Each MLIR file can contain multiple functions, generating multiple Verilog files
- **Function Extraction**: Automatically identifies and processes all top-level functions

#### **2. MLIR → Verilog Pipeline Stages**
1. **MLIR Optimization**: Applies comprehensive optimizations (affine passes, memref normalization, etc.)
2. **Loop Extraction**: Converts inner loops to functions (optional step)
3. **MLIR → FUTIL**: Converts optimized MLIR to Calyx FUTIL format using CIRCT
4. **FUTIL → Verilog**: Generates synthesizable Verilog using Calyx compiler

#### **3. Parameter Sweep Integration**
- **Automated Processing**: Each generated Verilog file undergoes FABulous preprocessing
- **Parameter Exploration**: Tests connectivity and congestion factor combinations
- **Synthesis Validation**: Measures synthesis success before placement/routing optimization
- **Comprehensive Metrics**: Tracks success rates at synthesis, placement, and routing stages

### ⚡ Key Advantages of MLIR Starting Point

1. **Direct Benchmark Input**: No need for C source compilation - works directly with MLIR files
2. **Multiple Function Support**: Single MLIR file can generate multiple benchmarks
3. **Optimization Control**: Applies consistent optimization passes to all benchmarks
4. **Scalable Processing**: Handles large sets of MLIR benchmarks automatically
5. **Error Isolation**: Identifies which MLIR functions successfully convert to working Verilog

### 📊 Enhanced Metrics and Analysis

- ✅ **MLIR Processing Success**: Tracks which MLIR files successfully generate Verilog
- 🔧 **Function-Level Analysis**: Per-function success rates within each MLIR benchmark
- 📁 **Benchmark Organization**: Groups results by original MLIR source file
- 🎛️ **Pipeline Stage Tracking**: Monitors success at MLIR→FUTIL→Verilog→Synthesis stages
- 📈 **Comparative Analysis**: Cross-benchmark performance comparisons

### 🗂️ File Organization Structure

```
BENCHMARK/
├── benchmark1.mlir          # Input MLIR files
├── benchmark2.mlir
└── benchmark3.mlir

generated_verilog/
├── benchmark1_func1.sv      # Generated Verilog files
├── benchmark1_func2.sv      # (multiple per MLIR file)
├── benchmark2_main.sv
└── benchmark3_loop.sv

parameter_sweep_results/
├── benchmark1_func1_conn0p0_cong0p0.json  # NextPNR results
├── benchmark1_func1_conn0p0_cong1p0.json  # (per Verilog file)
└── ...
```

### 🚨 Pipeline Validation Points

1. **MLIR File Discovery**: Validates BENCHMARK folder contains `.mlir` files
2. **Function Extraction**: Confirms functions are found in MLIR files
3. **FUTIL Generation**: Ensures MLIR→FUTIL conversion succeeds
4. **Verilog Generation**: Validates FUTIL→Verilog compilation
5. **Synthesis Validation**: Tests generated Verilog synthesizes correctly
6. **Parameter Sweep**: Runs placement/routing optimization on working designs

### 🎯 Usage Workflow

1. **Place MLIR Files**: Put unoptimized `.mlir` files in the BENCHMARK folder
2. **Run Pipeline**: Execute the notebook to process all MLIR files automatically
3. **Review Results**: Check synthesis success rates and parameter sweep outcomes
4. **Analyze Performance**: Use interactive dashboard to explore results
5. **Iterate**: Remove problematic MLIR files or adjust optimization passes

### 🔄 Benefits Over C-Based Pipeline

- **Simplified Input**: No C compilation or header file dependencies
- **Direct Control**: Work directly with MLIR intermediate representation  
- **Batch Processing**: Handle multiple MLIR benchmarks efficiently
- **Consistent Optimization**: Apply uniform optimization passes
- **Error Isolation**: Quickly identify problematic MLIR constructs
- **Function Granularity**: Generate multiple benchmarks from single MLIR file

This MLIR-centric approach provides a robust foundation for FPGA parameter optimization research, starting from a well-defined intermediate representation and ensuring consistent processing across all benchmarks.

### 🎉 Ready for Production

The notebook now serves as a complete MLIR-to-FPGA parameter optimization pipeline, providing comprehensive analysis from MLIR function extraction through nextpnr parameter tuning with detailed synthesis error tracking and interactive result visualization.